In [43]:
import pandas as pd

In [44]:
import plotly.graph_objects as go

In [45]:
import plotly.express as px

In [46]:
def fix_time(x):
    if not '+' in x:
        return 0
    else:  
        s = x.split(' ')
        if 'min' in x:
            return 60*int(s[1]) + int(s[-2])
        else:
            return int(s[-2])

In [47]:
df_giro = pd.read_csv('./data/giro.csv', sep=';', names=['position','name','team','time'])

In [48]:
df_giro['position'] = df_giro['position'].apply(lambda x:int(x.split('.')[0]))

In [49]:
df_giro['country'] = df_giro['name'].apply(lambda x:x.split(' ')[0])

In [50]:
df_giro['name'] = df_giro['name'].apply(lambda x:' '.join(x.split(' ')[1:]))

In [51]:
df_giro['time'] = df_giro['time'].apply(fix_time)

In [52]:
dict_flags = {
    'ITA':'🇮🇹',
    'NOR':'🇳🇴',
    'POR':'🇵🇹',
    'FRA':'🇫🇷',
    'NED':'🇳🇱',
    'BEL':'🇧🇪',
    'GER':'🇩🇪',
    'AUT':'🇦🇹',
    'RUS':'🇷🇺',
    'ESP':'🇪🇸',
    'USA':'🇺🇸',
    'HUN':'🇭🇺',
    'GBR':'🇬🇧',
    'COL':'🇨🇴',
    'IRL':'🇮🇪'
}

In [53]:
df_giro['country'].unique()

array(['ITA', 'NOR', 'POR', 'FRA', 'NED', 'BEL', 'GER', 'AUT', 'RUS',
       'ESP', 'USA', 'HUN', 'GBR', 'COL', 'IRL'], dtype=object)

In [54]:
df_giro['country'] = df_giro['country'].apply(lambda x:dict_flags[x])

In [55]:
df_giro['name'] = df_giro['country'] + ' ' + df_giro['name']

In [56]:
top_5_names = df_giro.tail(10).head(5)

In [57]:
format_time = lambda x:f'{x//60} min {x%60} seg'

In [58]:
for name in top_5_names.to_dict(orient='records'):
    print(f'{name["position"]}. {name["name"]} - {name["team"]}: +{format_time(name["time"])}')

1. 🇨🇴 Egan Bernal - Ineos Grenadiers: +0 min 0 seg
2. 🇮🇹 Damiano Caruso - Bahrain Victorious: +2 min 24 seg
3. 🇬🇧 Hugh Carthy - EF Education-Nippo: +3 min 40 seg
4. 🇷🇺 Aleksandr Vlasov - Astana-Premier Tech: +4 min 18 seg
5. 🇬🇧 Simon Yates - Team BikeExchange: +4 min 20 seg


In [59]:
top_5_names['name_position'] = top_5_names['position'].astype(str) + '. ' + top_5_names['name']

In [60]:
top_5_names.index = top_5_names['name']

In [61]:
top_5_names = top_5_names['name_position'].to_dict()

In [62]:
df_giro['name'] = df_giro['name'].apply(lambda x: top_5_names[x] if x in top_5_names else x)

In [63]:
stage = []
for n in range(len(df_giro)//10):
    stage = stage + [n+1]*10

In [64]:
df_giro['stage'] = stage

In [65]:
last_stage = df_giro['stage'].max()

In [66]:
df_giro = df_giro.loc[df_giro['stage']>=0]

In [67]:
names = df_giro.loc[
    (
        (df_giro['stage']==df_giro['stage'].max()) &
        (df_giro['position']<=5)
    ) #|
    #(
    #    (df_giro['position']==1)
    #)
]['name'].unique()

In [68]:
# df_giro = df_giro.loc[df_giro['name'].isin(names)]

In [69]:
df_giro = df_giro[
    [
        'name',
        'time',
        'stage'
    ]
]

In [70]:
time_max = df_giro['time'].max()

In [71]:
#time_max = (1+time_max//100)*100

In [72]:
time_max

601

In [73]:
df_giro = df_giro.pivot(
    columns=['name'],
    index='stage'
)['time']

In [74]:
df_giro = df_giro.fillna(time_max+30)

In [75]:
df_index = (pd.Series(list(range(1,max(df_giro.index)*100+1,1)), name='stage')/100).to_frame()

In [76]:
df_index = df_index.loc[df_index['stage']>=0]

In [77]:
df_giro = df_giro.reset_index()

In [78]:
df_giro['stage'] = df_giro['stage'].astype(float)

In [79]:
df_giro = pd.merge(df_index, df_giro, on='stage', how='left')

In [80]:
df_giro = df_giro.fillna(method='bfill')

In [81]:
df_giro = df_giro.rolling(100, win_type='triang').mean()

In [82]:
df_giro

stage  1. 🇨🇴 Egan Bernal  2. 🇮🇹 Damiano Caruso  3. 🇬🇧 Hugh Carthy  \
0        NaN                NaN                   NaN                NaN   
1        NaN                NaN                   NaN                NaN   
2        NaN                NaN                   NaN                NaN   
3        NaN                NaN                   NaN                NaN   
4        NaN                NaN                   NaN                NaN   
...      ...                ...                   ...                ...   
1595  15.465                0.0              143.8944           219.7152   
1596  15.475                0.0              143.9406           219.8398   
1597  15.485                0.0              143.9736           219.9288   
1598  15.495                0.0              143.9934           219.9822   
1599  15.505                0.0              144.0000           220.0000   

      4. 🇷🇺 Aleksandr Vlasov  5. 🇬🇧 Simon Yates  🇦🇹 Matthias Brändle  \
0                        NaN                NaN                  NaN   
1                        NaN                NaN                  NaN   
2                        NaN                NaN                  NaN   
3                        NaN                NaN                  NaN   
4                        NaN                NaN                  NaN   
...                      ...                ...                  ...   
1595                257.5488           259.4656                631.0   
1596                257.7462           259.6994                631.0   
1597                257.8872           259.8664                631.0   
1598                257.9718           259.9666                631.0   
1599                258.0000           260.0000                631.0   

      🇧🇪 Louis Vervaeke  🇧🇪 Remco Evenepoel  🇨🇴 Daniel Felipe Martínez  ...  \
0                   NaN                 NaN                        NaN  ...   
1                   NaN                 NaN                        NaN  ...   
2                   NaN                 NaN                        NaN  ...   
3                   NaN                 NaN                        NaN  ...   
4                   NaN                 NaN                        NaN  ...   
...                 ...                 ...                        ...  ...   
1595              631.0            629.7232                   436.3504  ...   
1596              631.0            630.2818                   436.6346  ...   
1597              631.0            630.6808                   436.8376  ...   
1598              631.0            630.9202                   436.9594  ...   
1599              631.0            631.0000                   437.0000  ...   

      🇮🇹 Diego Ulissi  🇮🇹 Edoardo Affini  🇮🇹 Filippo Ganna  🇮🇹 Gianni Moscon  \
0                 NaN                NaN               NaN               NaN   
1                 NaN                NaN               NaN               NaN   
2                 NaN                NaN               NaN               NaN   
3                 NaN                NaN               NaN               NaN   
4                 NaN                NaN               NaN               NaN   
...               ...                ...               ...               ...   
1595            631.0              631.0             631.0             631.0   
1596            631.0              631.0             631.0             631.0   
1597            631.0              631.0             631.0             631.0   
1598            631.0              631.0             631.0             631.0   
1599            631.0              631.0             631.0             631.0   

      🇮🇹 Giulio Ciccone  🇳🇱 Jos van Emden  🇳🇴 Tobias Foss  🇵🇹 João Almeida  \
0                   NaN               NaN             NaN              NaN   
1                   NaN               NaN             NaN              NaN   
2                   NaN               NaN             NaN              NaN   
3      

In [83]:
fig = go.Figure()

top_5_color_list = [
    #'#4E79A7',
    '#A0CBE8',
    #'#F28E2B',
    '#9C755F',
    '#59A14F',
    '#EDC948'
]

for name in df_giro.columns:
    if name != 'stage':
        line_dict = {
            'width':0.6
        }
        is_leader = list(df_giro.loc[df_giro['stage']==df_giro['stage'].max()][name])[0]==0
        if (name in names) and not is_leader:
            line_dict['color']=top_5_color_list.pop()
            line_dict['width']=4
        if is_leader:
            line_dict['color']='#FF8BC1'
            line_dict['width']=9
        fig.add_trace(
            go.Scatter(
                #x=list(df_giro['stage']) + [int(list(df_giro['stage'])[-1]+1)],
                #y=list(df_giro[name]) + [list(df_giro[name])[-1]],
                x=df_giro['stage']+0.7,
                y=df_giro[name],
                name=name,
                line=line_dict
            )
        )

fig.update_layout(
    yaxis = dict(title='Diferencia con el líder (segundos)'),
    yaxis_range=[time_max+10, -5]
    #yaxis_range=[370, -5]
)
fig.update_layout(
    xaxis = dict(
        title = 'Etapa',
        tickmode = 'linear',
        tick0 = 1,
        dtick = 1
    ),
    yaxis = dict(
        tickmode = 'linear',
        dtick = 60
    )
)
fig.update_layout(
    title = '🚴 Giro de Italia 🎀 Top 10 por etapa',
    title_x=0.25
)

fig.update_layout(legend_title_text=f'Top 5 en etapa {last_stage}')

for trace in fig['data']: 
    if (not trace['name'] in names):
        trace['showlegend'] = False
        
fig.layout.plot_bgcolor = '#eee'
fig.layout.paper_bgcolor = '#fff'

fig.show()

In [84]:
fig.write_html('../docs/giro.html')